# ABM and CellListMap

https://github.com/m3g/CellListMap.jl can quickly calculate partical pairs interactions within a cutoff.

Modeling the particle repulsion:

$$
\begin{align}
U(r) &= k_i k_j (r^2 - (r_i - r_j)^2)^2, \quad \text{for} r ≤ (r_i + r_j) \\
U(r) &= 0, \quad \text{otherwise}
\end{align}
$$

In [1]:
using Agents
using CellListMap
using CairoMakie
CairoMakie.activate!(px_per_unit = 1.0)

Define particle agents

In [2]:
@agent struct Particle(ContinuousAgent{2,Float64})
    r::Float64 ## radius
    k::Float64 ## repulsion force constant
    mass::Float64
end

Particle(; vel, r, k, mass) = (vel, r, k, mass)

Main.var"##240".Particle

Building the model

In [3]:
function initialize_bouncing(;
    number_of_particles=10_000,
    sides=SVector(500.0, 500.0),
    dt=0.001,
    max_radius=10.0,
    parallel=true
)
    # initial random positions
    positions = [sides .* rand(SVector{2,Float64}) for _ in 1:number_of_particles]

    # We will use CellListMap to compute forces, with similar structure as the positions
    forces = similar(positions)

    # Space for the agents
    space2d = ContinuousSpace(sides; periodic=true)

    # Initialize CellListMap particle system
    system = ParticleSystem(
        positions=positions,
        unitcell=sides,
        cutoff=2 * max_radius,
        output=forces,
        output_name=:forces, ## allows the system.forces alias for clarity
        parallel=parallel,
    )

    # define the ABModel properties
    # The system field contains the data required for CellListMap.jl
    properties = (;dt, number_of_particles, system)

    model = StandardABM(Particle,
        space2d;
        agent_step!,
        model_step!,
        agents_first = false,
        properties=properties
    )

    # Create active agents
    for id in 1:number_of_particles
        pos = positions[id]
        prop_particle = Particle(
            r = (0.5 + 0.9 * rand()) * max_radius,
            k = 10 + 20 * rand(), ## random force constants
            mass = 10.0 + 100 * rand(), ## random masses
            vel = 100 * randn(SVector{2}) ## initial velocities)
            )
        add_agent!(pos, Particle, model, prop_particle...)
    end

    return model
end

initialize_bouncing (generic function with 1 method)

Computing the repulsion force
It must follow CellListMap API and return a array for forces acting upon the particles

In [4]:
function calc_forces!(x, y, i, j, d2, forces, model)
    p_i = model[i]
    p_j = model[j]
    d = sqrt(d2)
    if d ≤ (p_i.r + p_j.r)
        dr = y - x ## x and y are minimum-image relative coordinates
        fij = 2 * (p_i.k * p_j.k) * (d2 - (p_i.r + p_j.r)^2) * (dr / d)
        forces[i] += fij
        forces[j] -= fij
    end
    return forces
end

calc_forces! (generic function with 1 method)

Update the pairwise forces using CellListMap API

In [5]:
function model_step!(model::ABM)
    map_pairwise!(
        (x, y, i, j, d2, forces) -> calc_forces!(x, y, i, j, d2, forces, model),
        model.system,
    )
    return nothing
end

model_step! (generic function with 1 method)

Update agent positions and velocity

In [6]:
function agent_step!(agent, model::ABM)
    id = agent.id
    dt = abmproperties(model).dt
    force = model.system.forces[id]
    acc = force / agent.mass
    # Update positions and velocities
    vel = agent.vel + acc * dt
    x = agent.pos + vel * dt + (acc / 2) * dt^2
    x = normalize_position(x, model)  ## Wraps agent position
    agent.vel = vel
    move_agent!(agent, x, model)
    # !!! Remember to update positions in the ParticleSystem
    model.system.positions[id] = agent.pos
    return nothing
end

agent_step! (generic function with 1 method)

Run simulation

In [7]:
function simulate(model=nothing; nsteps=1_000, number_of_particles=10_000)
    if isnothing(model)
        model = initialize_bouncing(number_of_particles=number_of_particles)
    end
    Agents.step!(model, nsteps)
end

simulate (generic function with 2 methods)

Test the performance

In [8]:
model = initialize_bouncing(number_of_particles=10_000)
@time simulate(model)

 10.546340 seconds (474.15 k allocations: 30.136 MiB, 469 lock conflicts, 3.64% compilation time)


StandardABM with 10000 agents of type Particle
 agents container: Dict
 space: periodic continuous space with [500.0, 500.0] extent and spacing=25.0
 scheduler: fastest
 properties: dt, number_of_particles, system

The helper function below is adapted from `Agents.abmvideo` and correctly displays animations in Jupyter notebooks

In [9]:
function abmvio(model;
    dt = 1, framerate = 30, frames = 300, title = "", showstep = true,
    figure = (size = (600, 600),), axis = NamedTuple(),
    recordkwargs = (compression = 23, format ="mp4"), kwargs...
)
    # title and steps
    abmtime_obs = Observable(abmtime(model))
    if title ≠ "" && showstep
        t = lift(x -> title*", time = "*string(x), abmtime_obs)
    elseif showstep
        t = lift(x -> "time = "*string(x), abmtime_obs)
    else
        t = title
    end

    axis = (title = t, titlealign = :left, axis...)
    # First frame
    fig, ax, abmobs = abmplot(model; add_controls = false, warn_deprecation = false, figure, axis, kwargs...)
    resize_to_layout!(fig)
    # Animation
    Makie.Record(fig; framerate, recordkwargs...) do io
        for j in 1:frames-1
            recordframe!(io)
            Agents.step!(abmobs, dt)
            abmtime_obs[] = abmtime(model)
        end
        recordframe!(io)
    end
end

abmvio (generic function with 1 method)

Visualize

In [10]:
model = initialize_bouncing(number_of_particles=1000)
vio = abmvio(
    model;
    framerate=20, frames=200, dt=5,
    title="Softly bouncing particles",
    agent_size=p -> p.r,
    agent_color=p -> p.k
)

vio |> display

Makie.VideoStream(Base.PipeEndpoint(RawFD(24) open, 0 bytes waiting), Process(setenv(`/home/runner/.julia/artifacts/fdb14f7b1bf6766687af4e3951c4d982cee66086/bin/ffmpeg -y -loglevel quiet -threads 4 -framerate 20 -pixel_format rgb24 -f rawvideo -s:v 600x600 -r 20 -i pipe:0 -vf vflip -profile:v high422 -crf 23 -preset slow -c:v libx264 -pix_fmt yuv420p -an '/tmp/jl_QQwpAA/##video#241.mp4'`,["JULIA_CI=true", "PATH=/home/runner/.julia/artifacts/b8a470e4553346122607f94ec60d83c77f061cd6/bin:/home/runner/.julia/artifacts/7f882b869c126a717e15be05453b83bd9135eab0/bin:/home/runner/.julia/artifacts/96bc7b9ddb319d1a051535c85184aa2bf42dbd8b/bin:/home/runner/.julia/artifacts/2a6bae048c28452d329375cbb7479499115e45ad/bin:/home/runner/.julia/artifacts/c8a20a2030f10b70947d8d2a6bff7f8b5f343fe9/bin:/home/runner/.julia/artifacts/0b5269206a6849e48487ed04136c30b1f12443e7/bin:/home/runner/.julia/artifacts/bdb4015047b09c6ac5002f73dfd5be8ddf59189b/bin:/home/runner/.julia/artifacts/00023f2f62a04af7531278ce1a689ff93800ffa1/bin:/home/runner/.julia/artifacts/a696e1e3e6b8d3c2c4b67609357ebc5c35eabde1/bin:/home/runner/.julia/artifacts/fdb14f7b1bf6766687af4e3951c4d982cee66086/bin:/opt/hostedtoolcache/julia/1.11.5/x64/bin:/opt/hostedtoolcache/uv/0.7.13/x86_64:/home/runner/.local/bin:/opt/hostedtoolcache/Python/3.13.5/x64/bin:/opt/hostedtoolcache/Python/3.13.5/x64:/snap/bin:/home/runner/.local/bin:/opt/pipx_bin:/home/runner/.cargo/bin:/home/runner/.config/composer/vendor/bin:/usr/local/.ghcup/bin:/home/runner/.dotnet/tools:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/usr/games:/usr/local/games:/snap/bin", "DOTNET_SKIP_FIRST_TIME_EXPERIENCE=1", "GITHUB_RUN_NUMBER=632", "GITHUB_REF_NAME=main", "RUNNER_ARCH=X64", "LD_LIBRARY_PATH=/home/runner/.julia/artifacts/715b660f53eb83c33e199a44ececfd8dc03f2a27/lib:/opt/hostedtoolcache/julia/1.11.5/x64/bin/../lib/julia:/home/runner/.julia/artifacts/94475b26c9b6ff3bed68391232c55fd81a4a64b4/lib:/home/runner/.julia/artifacts/b8a470e4553346122607f94ec60d83c77f061cd6/lib:/home/runner/.julia/artifacts/5acd766faaca59c3c1f3cfa67e2bf6dcf1e3e883/lib:/home/runner/.julia/artifacts/d4c2f2966f2932e4870b0488c3b8a6b92b6641a9/lib:/home/runner/.julia/artifacts/7f882b869c126a717e15be05453b83bd9135eab0/lib:/home/runner/.julia/artifacts/dc526f26fb179a3f68eb13fcbe5d2d2a5aa7eeac/lib:/home/runner/.julia/artifacts/1d90be1fb2a7f5023513bdcbb8abf7727ded6044/lib:/home/runner/.julia/artifacts/f8704eb01ec7508ae1f125b7ff89647997ed80cb/lib:/home/runner/.julia/artifacts/e8574c15e0152044b131e5d6956374f4b0bacce7/lib:/home/runner/.julia/artifacts/0c4797c296c27a8877ac9b42c35986da71cd14c7/lib:/home/runner/.julia/artifacts/f5e52a42c85b68d1f7ee821d9d8c13a44c377956/lib:/home/runner/.julia/artifacts/96bc7b9ddb319d1a051535c85184aa2bf42dbd8b/lib:/home/runner/.julia/artifacts/2a6bae048c28452d329375cbb7479499115e45ad/lib:/home/runner/.julia/artifacts/0a1006d282bce91b5cd408c714cbb95d3bb4f515/lib:/home/runner/.julia/artifacts/59eff635528e6914e1a96db241e950195574903b/lib:/home/runner/.julia/artifacts/299dd9a174ebc497df2cf4d30f1c6d10948c60ef/lib:/home/runner/.julia/artifacts/f0557b9a3c2c4667444e8fc63c1fc9c2c5cb9e63/lib:/home/runner/.julia/artifacts/6da9d8475fd9fd2867e3bd1f46f3913c800a316f/lib:/home/runner/.julia/artifacts/a3f956e6772ef4da35e128fd2a4477cf16fd3c84/lib:/home/runner/.julia/artifacts/e2512e1cd411449b9bede7b4294c7409c9973345/lib:/home/runner/.julia/artifacts/ed48bfcf31d2d5ebdc0a681d1ed07e1e9f9f0377/lib:/home/runner/.julia/artifacts/eb13375496c29fe52101a0e6710c54ff87aa0e20/lib:/home/runner/.julia/artifacts/5c030ff72c13f84fbbc8f93a146e34c6219a0261/lib:/home/runner/.julia/artifacts/bd1f25e7053ebc00ee7d82f3c5ec4cf1e9a51e17/lib:/home/runner/.julia/artifacts/cf5d5f8a6109be3f9c460a39768f57a3e53ff11d/lib:/home/runner/.julia/artifacts/c8a20a2030f10b70947d8d2a6bff7f8b5f343fe9/lib:/home/runner/.julia/artifacts/0631e2a6a31b5692eec7a575836451b16b734ec0/lib:/home/runner/.julia/artifacts/4abd0521d210cb9e48ea5e711873ba34dc05fc70/lib:/home/runner/.julia/artifacts/0b

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*